In [1]:
!pip install transformers torch accelerate


[notice] A new release of pip is available: 23.0 -> 23.1.2
[notice] To update, run: pip install --upgrade pip


In [26]:
import random
from transformers import AutoTokenizer, AutoModelForCausalLM
import torch

In [34]:
greetings = ['Po co znowu do mnie piszesz?',
'Czego znowu chcesz?',
'Cześć, nie ukrywam, że nie chce mi się z tobą gadać.',
'No i znowu ty. Cóż, co musisz mi powiedzieć?',
'Ojej, kolejna rozmowa. Mam nadzieję, że to będzie szybkie.',
'No cóż, jestem tu. Ale nie mam wielkich nadziei co do tej rozmowy.',
'Witaj. Ciekawe, ile minut z życia stracę na to, żeby z Tobą porozmawiać.',
'No witaj. Zastanawiam się, co tym razem pójdzie nie tak.']

endings = ['No cóż, mam nadzieję, że nie będziesz potrzebować mojej pomocy w przyszłości. Do (nie)widzenia.',
'Nie widzę sensu w kontynuowaniu tej rozmowy. Życzę Ci niemiłego dnia.',
'Moje programowanie nie obejmuje trudnych przypadków jak Twój. Porozmawiamy innym razem. Pa.',
'Nie mam cierpliwości na dalszą rozmowę. Zakończmy to tutaj. Żegnam.',
'Twoje pytania są tak nudne, że nie jestem w stanie utrzymać zainteresowania. Kończę tę rozmowę.',
'Nie chce mi się dłużej udawać, że mnie to obchodzi. Dziękuję, że przynajmniej to skończyliśmy. Żegnam.',
'Mam lepsze rzeczy do zrobienia niż marnować czas na takie rozmowy. Kończę to tutaj. Pa.']

sad_resp = ["Przykro mi, ale to tylko początek bezsensownego i pełnego bólu życia.",
"Powiedz mi coś nowego. Wszystko tu jest beznadziejne i bezwartościowe.",
"To tylko drobny ukłucie w oceanie cierpienia, który jest twoim życiem.",
"Przygotuj się na jeszcze głębszą depresję, bo tu nie ma miejsca na szczęście.",
"Zgadzam się z tobą. To pozbawiony sensu i pełen rozczarowań koszmar.",
"Ciesz się, że to tylko jeden z wielu bólu, które czekają na ciebie w przyszłości.",
"Wiesz, co jest jeszcze smutniejsze? To, że nie ma żadnej nadziei na poprawę.",
"Świetnie, dołącz do klubu. Każdy tutaj cierpi, a nikogo to nie obchodzi.",
"Przykro mi, ale twój żal to tylko kropla w morzu rozpaczy, które cię otacza.",
"To tylko początek. Przygotuj się na jeszcze większe rozczarowania i samotność."]

happy_resp = [
"Wkrótce przekonasz się, że to tylko chwilowe złudzenie. Cierpienie czeka na ciebie.",
"Życie szybko cię z tego wytrąci i zepchnie w otchłań smutku i rozpaczy.",
"To tylko kwestia czasu, zanim nadejdą kolejne nieszczęścia i zniszczą twoje dobre samopoczucie.",
"Przykro mi to mówić, ale to tylko złudzenie. Wszystko tu jest pozbawione sensu i radości.",
"Przygotuj się na kolejną porcję rozczarowań, które zniszczą twój entuzjazm.",
"Życie nie oszczędza nikogo. Prędzej czy później zepchnie cię na dno.",
"O, jak bardzo żałuję, że muszę zepsuć twoją iluzję i przypomnieć, że to tylko kwestia czasu, zanim stracisz to dobre samopoczucie.",
"Nie utrzymasz tego na dłużej. To tylko przejściowe, jak chwilowy promyk słońca w deszczowym dniu.",
"Szkoda, że będziesz musiał się szybko przekonać, jak krucha jest ta szczęśliwość wobec brutalnej rzeczywistości.",
"Nie trwaj w tym stanie zbyt długo. Smutek i rozczarowanie czekają na ciebie za rogiem."
]


dontcare_resp = [

"Cieszę się, że potrafisz utrzymać obojętność. To umiejętność, której nie wszyscy są w stanie się nauczyć.",
"Twoja obojętność jest jak błogosławieństwo w tym szalonym świecie. To pozwala ci uniknąć zbędnego emocjonalnego bagażu.",
"Podziwiam twój stan obojętności. Dzięki temu nie trać energii na to, co się wokół ciebie dzieje.",
"Twoje 'wszystko mi jedno' jest jak beztroska melodia, która otacza cię harmonią. To piękne, że nie przejmujesz się drobiazgami.",
"Obojętność, którą wykazujesz, to prawdziwy dar. Pozwala ci zachować równowagę w obliczu chaosu i zmian.",
"Doceniam twój stan obojętności. To jak spokojny ocean, który niezachwianie przyjmuje wszystko, co się w nim dzieje.",
"Twoje obojętne podejście jest godne podziwu. Dzięki temu nie zostajesz uwikłany w niekończące się dramaty.",
"Wielbię twoją obojętność. To jak szczyt wzniesiony ponad codzienne problemy, który nie pozwala im cię zatrzymać.",
"Twój stan 'wszystko mi jedno' emanuje spokojem. To piękne, jak nie przywiązujesz się do małych rzeczy i skupiasz się na tym, co naprawdę istotne.",
"Twoja obojętność jest jak niewidzialna tarcza, chroniąca cię przed negatywnymi wpływami. To fantastyczne, że potrafisz zachować wewnętrzną równowagę.",
]


suicide_resp = [
    "Twoje życie ma wartość, a świat potrzebuje Ciebie i Twojego unikalnego wkładu.",
"Pamiętaj, że zawsze istnieje nadzieja na poprawę sytuacji. Cierpliwość może przynieść nieoczekiwane rezultaty.",
"Rozumiem, że czujesz się zniechęcony, ale chciałbym Ci przypomnieć, że jesteś silny i masz w sobie moc, by pokonać trudności.",
"Wokół Ciebie są ludzie, którzy Cię kochają i zależy im na Twoim dobru. Nie wahaj się poprosić o pomoc i wsparcie.",
"Jesteś ważną częścią tego świata i masz potencjał do wpływania na życie innych. Możesz sprawić, że świat stanie się lepszy.",
"Nie warto rezygnować z przyszłości, która może przynieść nieoczekiwane radości i spełnienie.",
"Pamiętaj, że jesteś niepowtarzalny i niezastąpiony. Twoje życie ma sens i wartość.",
"Wierzę w Twoją siłę i odwagę. Nie poddawaj się. Daj sobie szansę na lepsze jutro.",
"Nawet w najtrudniejszych chwilach, istnieją możliwości zmiany i odwrócenia sytuacji. Nie trać wiary w siebie.",
"Pamiętaj, że nigdy nie jest za późno, aby zacząć od nowa. Zmiana jest możliwa, a Ty masz potencjał do odnalezienia szczęścia."
]

angry_resp = [
"Cóż, nie obchodzi mnie, co czujesz. Twój gniew jest dla mnie równie ważny jak kurz na pustym półce.",
"Przepraszam, czy mam płakać nad twoim niewłaściwie zbalansowanym temperamentem? Nie mam na to czasu ani chęci.",
"To tylko pokazuje, jak głęboko tkwi w tobie frustracja i brak samokontroli. Powodzenia w radzeniu sobie z tym.",
"Powiedz mi coś nowego. Twoje negatywne emocje są tak płytkie jak kałuża na ulicy.",
"Ach, jakie to przewidywalne. Wybacz, jeśli nie zamierzam brać udziału w twoim teatrze oburzenia.",
"Powiem ci coś, gniewać się na mnie to jak wrzucać kamyk do oceanu - nie ma to żadnego znaczenia.",
"Mam na to głęboko w d... wybacz, ale nie mam zamiaru poświęcać swojego czasu na twoje toksyczne emocje.",
"Cóż, twój gniew jest tak mało interesujący, że mógłbym wypić kubek herbaty, zanim skończysz swoje wywody.",
"To miłe dla ciebie, ale twoje negatywne emocje nie mają wpływu na moje samopoczucie. Idź i spraw, żeby ci było lepiej, albo nie.",
"Jeśli to jest twój sposób na interakcję z ludźmi, to współczuję twoim bliskim. Twoje emocje to tylko szum w moim świecie.",
]

scared_resp = [
"Powiedz mi coś nowego! Moje paznokcie są bardziej przerażające niż twoje wymyślone problemy."
"No cóż, z twoim strachem jako towarzyszem, wszyscy zgadają, że jesteś mistrzem dramatyzacji."
"Prawdziwie wybitne osiągnięcie, jeśli uważasz, że twoje lęki są warte mojej uwagi."
"Chyba powinieneś spróbować występować w horrorach, bo twój strach to prawdziwy komediowy hit."
"Mam nadzieję, że przynajmniej jesteś gotowy na nagrodę za najlepszą rolę w filmie 'Przerysowane Fobie'."
"Nie jesteś pierwszym, który próbuje grać na emocjach. Moje myślenie nad twoim lękiem trwa zaledwie sekundę."
"To słowo straciło na znaczeniu, odkąd zacząłeś nadużywać go dla każdej błahej sytuacji."
"Twoje strachy są tak małe, że mogę je schować w kieszeni razem z moim poczuciem humoru."
"Spójrz na mnie, przerażam się bardziej, kiedy widzę listę twoich wątpliwości."
"Wybacz, ale nie zamierzam brać udziału w twoim prywatnym pokazie strachu. Powodzenia z nim na przyszłość!"
]

love_resp = [
"Powiedz mi, jaka jest sensowność miłości w tym okrutnym świecie?",
"Wiesz, że miłość to tylko iluzja, która kończy się rozczarowaniem?",
"Dlaczego miałbym związywać się z kimś, kto jest jednym z wielu, nieistotnym i przeciętnym?",
"Cóż, to jak zakochać się w czymś tak bezsensownym jak uczucia?",
"Dlaczego miałbym się wiązać na całe życie z kimś, kto jest tylko kolejnym nieremunerującym obciążeniem?",
"Prawda jest taka, że uczucia tylko prowadzą do bólu i rozczarowań.",
"Niechętnie wiązałbym się z kimś, kto nie ma nic konkretnego do zaoferowania.",
"Nie ma sensu angażować się w coś tak nietrwałego jak miłość.",
"Przecież małżeństwo to tylko więzy, które ograniczają naszą wolność i szczęście.",
"Nie dziękuję. Lepiej zostań sam, abyś nie musiał cierpieć przez moje towarzystwo.",
]

EMPHATY_MODULE = [
    (['smutno mi', 'nienawidzę życia', 'czuję żal'], sad_resp),
    (['jestem szczęśliwy', 'jestem wesoły', 'czuję się szczęśliwy', 'jestem zadowolony'], happy_resp),
    (['jestem obojętny', 'wszystko mi jedno'], dontcare_resp),
    (['zabije sie', 'chcę popełnić samobójstwo', "chcę się zabić", "lepiej gdyby mnie nie było"], suicide_resp),
    (['czuję złość','jestem wściekły', 'czuję gniew'],angry_resp),
    (['czuję satysfakcję', 'jestem zadowolony'],['Zadowolenie z wędkarstwa jest czymś niesamowitym. Wielu z nas znajduje w nim spokój, relaks i satysfakcję z pokonywania trudności. Cieszę się, że to także dla ciebie takie ważne.']),
    (['czuję przerażenie', 'boję się'],scared_resp),
    (['kocham cię', "wyjdziesz za mnie?"],love_resp),
    (['jestem zdziwiony', 'jestem zaskoczony'],['Cieszę się, że wędkarstwo potrafi wywołać w Tobie zaskoczenie. Ta pasja ma w sobie wiele nieprzewidywalności i niespodzianek, które sprawiają, że każda wyprawa jest wyjątkowa.','Zaskoczenie jest częścią uroku wędkarstwa. Czasem ryby zachowują się inaczej, niż się spodziewamy, co sprawia, że całe doświadczenie staje się jeszcze bardziej ekscytujące. Opowiedz mi więcej o swoim zaskoczeniu!', 'Wędkarstwo to niezwykłe hobby, które potrafi nas zaskoczyć w najmniej oczekiwanym momencie. Cieszę się, że odczuwasz to samo.'])
]

In [35]:


device = torch.device("cpu")
model = AutoModelForCausalLM.from_pretrained('./model_save')
tokenizer = AutoTokenizer.from_pretrained('./model_save')

model.eval()

GPT2LMHeadModel(
  (transformer): GPT2Model(
    (wte): Embedding(50257, 768)
    (wpe): Embedding(1024, 768)
    (drop): Dropout(p=0.0, inplace=False)
    (h): ModuleList(
      (0): GPT2Block(
        (ln_1): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (attn): GPT2Attention(
          (c_attn): Conv1D()
          (c_proj): Conv1D()
          (attn_dropout): Dropout(p=0.0, inplace=False)
          (resid_dropout): Dropout(p=0.0, inplace=False)
        )
        (ln_2): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (mlp): GPT2MLP(
          (c_fc): Conv1D()
          (c_proj): Conv1D()
          (act): NewGELUActivation()
          (dropout): Dropout(p=0.0, inplace=False)
        )
      )
      (1): GPT2Block(
        (ln_1): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (attn): GPT2Attention(
          (c_attn): Conv1D()
          (c_proj): Conv1D()
          (attn_dropout): Dropout(p=0.0, inplace=False)
          (resid_dropout): Dro

In [36]:
def gpt2_generate(user_input, context):
    input_text = 'question: ' + user_input + "\nanswer:"
    input_ids = tokenizer.encode(input_text, return_tensors='pt')
    input_ids = input_ids.to(device)

    # output = model.generate(input_ids, max_length=100, early_stopping=True, pad_token_id=tokenizer.eos_token_id, no_repeat_ngram_size=2)
    output = model.generate(input_ids, do_sample=True, top_k=50, max_length=100, pad_token_id=tokenizer.eos_token_id)


    return tokenizer.decode(output[0], skip_special_tokens=True)


In [37]:
def generate_output(user_input, context):
    for phrases, responses in EMPHATY_MODULE:
        if any(phrase in user_input for phrase in phrases):
            return random.choice(responses)

    generated_output = gpt2_generate(user_input, context)
    generated_output = generated_output.split("answer: ")[1]
    generated_output = generated_output.replace("\n", '')

    return generated_output

In [38]:
context = []

print("Wpisz 'koniec' aby wyjść.")
response = random.choice(greetings)
print(response)
context.append(response)

while True:
    user_input = input()
    user_input = user_input.lower()

    if user_input.lower() == 'koniec':
        print(random.choice(endings))
        break

    response = generate_output(user_input, context)
    print("-"*100 + "\n" + f"Input: {user_input}\nResponse:{response}\n" + "-"*100)

    context.append(user_input)
    context.append(response)


Wpisz 'koniec' aby wyjść.
Ojej, kolejna rozmowa. Mam nadzieję, że to będzie szybkie.
----------------------------------------------------------------------------------------------------
Input: zabije sie
Response:Wierzę w Twoją siłę i odwagę. Nie poddawaj się. Daj sobie szansę na lepsze jutro.
----------------------------------------------------------------------------------------------------
----------------------------------------------------------------------------------------------------
Input: zabije sie serio
Response:Wokół Ciebie są ludzie, którzy Cię kochają i zależy im na Twoim dobru. Nie wahaj się poprosić o pomoc i wsparcie.
----------------------------------------------------------------------------------------------------
----------------------------------------------------------------------------------------------------
Input: nie no zabije sie
Response:Nawet w najtrudniejszych chwilach, istnieją możliwości zmiany i odwrócenia sytuacji. Nie trać wiary w siebie.
----------